# LLooM: Getting Started - Template Notebook

Last Updated: April 2024

### Installation
First, install the LLooM Python package, available on PyPI as [`text_lloom`](https://pypi.org/project/text_lloom/). We recommend setting up a virtual environment with [venv](https://docs.python.org/3/library/venv.html#creating-virtual-environments) or [conda](https://conda.io/projects/conda/en/latest/user-guide/tasks/manage-environments.html#creating-an-environment-with-commands).

In [32]:
!pip install text_lloom --quiet

In [33]:
!pip install pyserial

Defaulting to user installation because normal site-packages is not writeable


In [34]:
import nltk
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to
[nltk_data]     /home/lbartolome/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

### Imports

In [83]:
import os
import pandas as pd
import numpy as np
from dotenv import load_dotenv
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)

LLooM uses the OpenAI API under the hood to support its core operators (using GPT-3.5 and GPT-4). You'll first need to locally set the `OPENAI_API_KEY` variable to use your own account.

In [84]:
# Please enter in your OpenAI key "sk-123xyz" below.
load_dotenv('/export/usuarios_ml4ds/lbartolome/Repos/repos_con_carlos/RAG_tool/.env')
os.environ["OPENAI_API_KEY"] = os.getenv("OPENAI_API_KEY")

In [85]:
# Import the LLooM package:
import text_lloom.workbench as wb

### Load data
For this example, we'll be using a sample dataset of 100 **Facebook posts** from **political** pages, gathered via CrowdTangle. The main columns we'll be using in our analysis are the following:
- `doc_id`: Unique ID for each post
- `text`: The text of the Facebook post
- `Page Category`: The category of the Facebook page
- `Likes`: The number of "likes" that the post received

In [95]:
# We'll load data from an existing CSV
# data_link = "https://michelle123lam.github.io/lloom/data/political_fb_posts_100.csv"
# data_link = "/content/NCTE_transcript.csv"
# df = pd.read_csv(data_link)

data_link = '/export/usuarios_ml4ds/cggamella/RAG_tool/files/anotacion_manual/fam/datos_modelo_es_Mallet_df_merged_14_topics_45_ENTREGABLE.parquet'
data_link = '/export/usuarios_ml4ds/cggamella/RAG_tool/files/anotacion_manual/fam/S2_Kwds3_AI_with_text_30000.parquet'
df = pd.read_parquet(data_link)
df.head(3)

id      pmid                      doi    year  \
0   3091      None    10.1145/505282.505283  2001.0   
1  17043  17149504   10.1055/s-0038-1634127  2006.0   
2  62989      None  10.21917/IJSC.2013.0095  2013.0   

                                                                                            title  \
0                                               Machine learning in automated text categorization   
1                  Bayesian Random-effect Model for Predicting Outcome Fraught with Heterogeneity   
2  ONTOLOGY BASED MEANINGFUL SEARCH USING SEMANTIC WEB AND NATURAL LANGUAGE PROCESSING TECHNIQUES   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     paperAbstract  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     The automated categorization (or classification) of texts into predefined categories has witnessed a booming interest in the last 10 years, due to the increased availability of documents in digital form and the ensuing need to organize them. In the research community the dominant approach to this problem is based on machine learning techniques: a general inductive process automatically builds a classifier by learning, from a set of preclassified documents, the characteristics of the categories. The advantages of this approach over the knowledge engineering approach (consisting in the manual definition of a classifier by domain experts) are a very good effectiveness, considerable savings in terms of expert labor power, and straightforward portability to different domains. This survey discusses the main approaches to text categorization that fall within the machine learning paradigm. We will discuss in detail issues pertaining to three different problems, namely, document representation, classifier construction, and classifier evaluation.   
1  Summary Objective: The study aimed to develop a predictive model to d

In [87]:
len(df)

34257

In [88]:
# df.head(10)
df.keys()

Index(['identifier', 'id_tm', 'texto_preprocesado', 'texto_sin_preprocesar',
       'CPV'],
      dtype='object')

In [96]:
#df.rename(columns={'id_tm': 'doc_id', 'texto_sin_preprocesar': 'text'}, inplace=True)
df.rename(columns={'id': 'doc_id', 'texto_sin_preprocesar': 'text'}, inplace=True)

In [97]:
# Preview of dataframe
display(df[["doc_id", "text"]].head())

doc_id  \
0    3091   
1   17043   
2   62989   
3   79336   
4  149368   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            text  
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [98]:
len(df)

30000

In [99]:
df = df[:100]

In [100]:
df = df.drop_duplicates(subset=['doc_id'], keep='first')
len(df)

100

## v1: Manual mode

This notebook shows two example workflows: **v1: Manual mode**, or **v2: Auto mode**. We recommend starting with **v1: Manual mode** to survey the LLooM concepts and get a sense for the underlying functions.

### Create a LLooM instance
Then, after loading your data as a Pandas DataFrame, create a new LLooM instance. You will need to specify the name of the column that contains your input text documents (`text_col`). The ID column (`id_col`) is optional.

In [102]:
# Set up the LLooM instance with the specified dataset
l = wb.lloom(
    df=df,
    text_col="text",
    id_col="doc_id",  # Optional
)

### Run concept generation
Next, you can go ahead and start the concept induction process by generating concepts. You can omit the `seed` parameter if you do not want to use a seed.

In [103]:
cur_seed = None  # Optionally replace with string
await l.gen(seed=cur_seed)

N sentences: Median=7, Std=4.65
Auto-suggested parameters: {'filter_n_quotes': 6, 'summ_n_bullets': 4, 'synth_n_concepts': 6}


Estimated cost: $0.2
**Please note that this is only an approximate cost estimate**


Action required


Proceed with generation? (y/n):  y




Distill-filter
⠼ Loading Error Error code: 404 - {'error': {'message': 'Invalid URL (POST /v1/chat/completions)', 'type': 'invalid_request_error', 'param': None, 'code': None}}
⠧ Loading Error Error code: 404 - {'error': {'message': 'Invalid URL (POST /v1/chat/completions)', 'type': 'invalid_request_error', 'param': None, 'code': None}}
✅ Done    


doc_id  \
0      3091   
1     17043   
2     62989   
3     79336   
4    149368   
5    160975   
6    167440   
7    203938   
8    218714   
9    239550   
10   274182   
11   370987   
12   393276   
13   398740   
14   460154   
15   484385   
16   544202   
17   566799   
18   574675   
19   590390   
20   619169   
21   719526   
22   740603   
23   770069   
24   812443   
25   837233   
26   868597   
27   870824   
28   943198   
29   991860   
30  1018689   
31  1054277   
32  1105629   
33  1211007   
34  1214376   
35  1316911   
36  1392988   
37  1413358   
38  1421248   
39  1440500   
40  1481102   
41  1486468   
42  1498296   
43  1555772   
44  1628976   
45  1639829   
46  1653033   
47  1697493   
48  1867612   
49  1869728   
50  1909530   
51  1930958   
52  1940772   
53  1970173   
54  1995967   
55  2094096   
56  2112552   
57  2156731   
58  2203482   
59  2204200   
60  2205400   
61  2254495   
62  2330463   
63  2354883   
64  2387309   
65  2404842   
66  2424684   
67  2474316   
68  2504652   
69  2527482   
70  2548177   
71  2638032   
72  2775420   
73  2868403   
74  2959311   
75  2992648   
76  2999464   
77  3010493   
78  3020703   
79  3062984   
80  3262484   
81  3401601   
82  3417178   
83  3420416   
84  3420849   
85  3462007   
86  3490142   
87  3504932   
88  3666697   
89  3667489   
90  3709816   
91  3790606   
92  3840954   
93  3935763   
94  3982334   
95  4029020   
96  4412524   
97  4562897   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 text  
0                                                                                                                                                                                                                                                                                                    The automated categorization (or classification) of texts into predefined categories has witnessed a booming interest in the last 10 years, due to the increased availability of documents in digital form and the ensuing need to organize them.\nIn the research community the dominant approach to this problem is based on machine learning techniques: a general inductive process automatically builds a classifier by learning, from a set of preclassified documents, the characteristics of the categories.\nThe advantages of this approach over the knowledge engineering approach (consisting in the manual definition of a classifier by domain experts) are a very good effectiveness, considerable savings in terms of expert labor power, and straightforward portability to different domains.\nThis survey discusses the main approaches to text categorization that fall within the mac



Distill-summarize
⠦ Loading Error Error code: 404 - {'error': {'message': 'Invalid URL (POST /v1/chat/completions)', 'type': 'invalid_request_error', 'param': None, 'code': None}}
✅ Done    


doc_id  \
0       3091   
1       3091   
2       3091   
3       3091   
4      17043   
5      17043   
6      17043   
7      17043   
8      62989   
9      62989   
10     62989   
11     62989   
12     79336   
13     79336   
14     79336   
15     79336   
16    149368   
17    149368   
18    149368   
19    149368   
20    160975   
21    160975   
22    160975   
23    160975   
24    167440   
25    167440   
26    167440   
27    167440   
28    203938   
29    203938   
30    203938   
31    203938   
32    218714   
33    218714   
34    218714   
35    218714   
36    239550   
37    239550   
38    239550   
39    239550   
40    274182   
41    274182   
42    274182   
43    274182   
44    370987   
45    370987   
46    370987   
47    370987   
48    393276   
49    393276   
50    393276   
51    393276   
52    398740   
53    398740   
54    398740   
55    398740   
56    460154   
57    460154   
58    460154   
59    460154   
60    484385   
61    484385   
62    484385   
63    484385   
64    544202   
65    544202   
66    544202   
67    544202   
68    566799   
69    566799   
70    566799   
71    566799   
72    574675   
73    574675   
74    574675   
75    574675   
76    590390   
77    590390   
78    590390   
79    590390   
80    619169   
81    619169   
82    619169   
83    619169   
84    719526   
85    719526   
86    719526   
87    719526   
88    740603   
89    740603   
90    740603   
91    740603   
92    770069   
93    770069   
94    770069   
95    770069   
96    812443   
97    812443   
98    812443   
99    812443   
100   837233   
101   837233   
102   837233   
103   837233   
104   868597   
105   868597   
106   868597   
107   868597   
108   870824   
109   870824   
110   870824   
111   870824   
112   943198   
113   943198   
114   943198   
115   943198   
116   991860   
117   991860   
118   991860   
119   991860   
120  1018689   
121  1018689   
122  1018689   
123  1018689   
124  1054277   
125  1054277   
126  1054277   
127  1054277   
128  1105629   
129  1105629   
130  1105629   
131  1105629   
132  1211007   
133  1211007   
134  1211007   
135  1211007   
136  1214376   
137  1214376   
138  1214376   
139  1214376   
140  1316911   
141  1316911   
142  1316911   
143  1316911   
144  1392988   
145  1392988   
146  1392988   
147  1392988   
148  1413358   
149  1413358   
150  1413358   
151  1413358   
152  1421248   
153  1421248   
154  1421248   
155  1421248   
156  1440500   
157  1440500   
158  1440500   
159  1440500   
160  1481102   
161  1481102   
162  1481102   
163  1481102   
164  1486468   
165  1486468   
166  1486468   
167  1486468   
168  1498296   
169  1498296   
170  1498296   
171  1498296   
172  1555772   
173  1555772   
174  1555772   
175  1555772   
176  1628976   
177  1628976   
178  1628976   
179  1628976   
180  1639829   
181  1639829   
182  1639829   
183  1639829   
184  1653033   
185  1653033   
186  1653033   
187  1653033   
188  1697493   
189  1697493   
190  1697493   
191  1697493   
192  1867612   
193  1867612   
194  1867612   
195  1867612   
196  1869728   
197  1869728   
198  1869728   
199  1869728   
200  1909530   
201  1909530   
202  1909530   
203  1909530   
204  1930958   
205  1930958   
206  1930958   
207  1930958   
208  1940772   
209  1940772   
210  1940772   
211  1940772   
212  1970173   
213  1970173   
214  1970173   
215  1970173   
216  1995967   
217  1995967   
218  1995967   
219  1995967   
220  2094096   
221  2094096   
222  2094096   
223  2094096   
224  2156731   
225  2156731   
226  2156731   
227  2156731   
228  2203482   
229  2203482   
230  2203482   
231  2203482   
232  2204200   
233  2204200   
234  2204200   
235  2204200   
236  2205400   
237  2205400   
238  2205400   
239  2205400   
240  2254495   
241  2254495   
242  2254495   
243  2254495   
244  2330463   
245  2330463   
246  2330463   
247  2330463   
248  2354883   
249  2



Cluster
✅ Done    


doc_id  \
0       3091   
264  2474316   
263  2424684   
262  2424684   
261  2424684   
260  2424684   
259  2404842   
258  2404842   
257  2404842   
256  2404842   
265  2474316   
255  2387309   
253  2387309   
252  2387309   
251  2354883   
250  2354883   
249  2354883   
248  2354883   
247  2330463   
246  2330463   
245  2330463   
254  2387309   
244  2330463   
266  2474316   
268  2504652   
288  2868403   
287  2775420   
286  2775420   
285  2775420   
284  2775420   
283  2638032   
282  2638032   
281  2638032   
280  2638032   
267  2474316   
279  2548177   
277  2548177   
276  2548177   
275  2527482   
274  2527482   
273  2527482   
272  2527482   
271  2504652   
270  2504652   
269  2504652   
278  2548177   
243  2254495   
242  2254495   
241  2254495   
215  1970173   
214  1970173   
213  1970173   
212  1970173   
211  1940772   
210  1940772   
209  1940772   
208  1940772   
207  1930958   
216  1995967   
206  1930958   
204  1930958   
203  1909530   
202  1909530   
201  1909530   
200  1909530   
199  1869728   
198  1869728   
197  1869728   
196  1869728   
205  1930958   
217  1995967   
218  1995967   
219  1995967   
240  2254495   
239  2205400   
238  2205400   
237  2205400   
236  2205400   
235  2204200   
234  2204200   
233  2204200   
232  2204200   
231  2203482   
230  2203482   
229  2203482   
228  2203482   
227  2156731   
226  2156731   
225  2156731   
224  2156731   
223  2094096   
222  2094096   
221  2094096   
220  2094096   
289  2868403   
195  1867612   
290  2868403   
292  2959311   
361  3790606   
360  3790606   
359  3709816   
358  3709816   
357  3709816   
356  3709816   
355  3667489   
354  3667489   
353  3667489   
362  3790606   
352  3667489   
350  3666697   
349  3666697   
348  3666697   
347  3504932   
346  3504932   
345  3504932   
344  3504932   
343  3490142   
342  3490142   
351  3666697   
341  3490142   
363  3790606   
365  3840954   
385  4562897   
384  4562897   
383  4412524   
382  4412524   
381  4412524   
380  4412524   
379  4029020   
378  4029020   
377  4029020   
364  3840954   
376  4029020   
374  3982334   
373  3982334   
372  3982334   
371  3935763   
370  3935763   
369  3935763   
368  3935763   
367  3840954   
366  3840954   
375  3982334   
340  3490142   
339  3462007   
338  3462007   
312  3062984   
311  3020703   
310  3020703   
309  3020703   
308  3020703   
307  3010493   
306  3010493   
305  3010493   
304  3010493   
313  3062984   
303  2999464   
301  2999464   
300  2999464   
299  2992648   
298  2992648   
297  2992648   
296  2992648   
295  2959311   
294  2959311   
293  2959311   
302  2999464   
314  3062984   
315  3062984   
316  3262484   
337  3462007   
336  3462007   
335  3420849   
334  3420849   
333  3420849   
332  3420849   
331  3420416   
330  3420416   
329  3420416   
328  3420416   
327  3417178   
326  3417178   
325  3417178   
324  3417178   
323  3401601   
322  3401601   
321  3401601   
320  3401601   
319  3262484   
318  3262484   
317  3262484   
291  2868403   
194  1867612   
193  1867612   
192  1867612   
69    566799   
68    566799   
67    544202   
66    544202   
65    544202   
64    544202   
63    484385   
62    484385   
61    484385   
70    566799   
60    484385   
58    460154   
57    460154   
56    460154   
55    398740   
54    398740   
53    398740   
52    398740   
51    393276   
50    393276   
59    460154   
49    393276   
71    566799   
73    574675   
93    770069   
92    770069   
91    740603   
90    740603   
89    740603   
88    740603   
87    719526   
86    719526   
85    719526   
72    574675   
84    719526   
82    619169   
81    619169   
80    619169   
79    590390   
78    590390   
77    590390   
76    590390   
75    574675   
74    574675   
83    619169   
48    393276   
47    370987   
46    370987   
20    160975   
19    149368   
18    149368   
17    149368   
16    149368   
15     79336   
14    



Synthesize
✅ Done    


Input examples: ['Text categorization using machine learning techniques', 'Machine learning for music genre classification', 'Experiments conducted on 9 Chinese-English test-sets', 'Special conversion rules ensure complete semantic structures', 'Improves BLEU score and reduces TER', 'Algorithm extracts SRL-aware SCFG rules', 'Optimizing decision trees in real-time', 'Training new decision trees quickly', 'Introducing an incremental decision tree algorithm', 'Adapting to new samples for classification', 'Inductive models for genre distinctions', 'EM interpretation with binary latent variables', 'Learn generative FRAME model using CNN filters', 'CNN successful in computer vision tasks', 'Potential for substantial improvements shown in examples', 'Local decision boundaries determined and neighborhoods modified', 'Effective metric estimated using local linear discriminant analysis', 'Locally adaptive nearest neighbor classification proposed', 'Efficiency of soluti

In [105]:
# View cost/time summary
l.summary()

Total time: 33.63 sec (0.56 min)
	('Distill-filter', '2024-09-15-19-11-04'): 6.47 sec
	('Distill-summarize', '2024-09-15-19-11-08'): 3.70 sec
	('Cluster', '2024-09-15-19-11-17'): 8.86 sec
	('Synthesize', '2024-09-15-19-11-27'): 9.92 sec
	('Review-remove', '2024-09-15-19-11-27'): 0.68 sec
	('Review-merge', '2024-09-15-19-11-31'): 4.00 sec


Total cost: $0.17
	('Distill-filter', '2024-09-15-19-11-04'): $0.039
	('Distill-summarize', '2024-09-15-19-11-08'): $0.018
	('Synthesize', '2024-09-15-19-11-27'): $0.102
	('Review-remove', '2024-09-15-19-11-27'): $0.003
	('Review-merge', '2024-09-15-19-11-31'): $0.008


Tokens: total=84969, in=64019, out=20950


### Review concepts

Review the generated concepts and select concepts to inspect further:

In [47]:
!jupyter nbextension enable --py widgetsnbextension

Traceback (most recent call last):
  File "/Server/python/anaconda3/bin/jupyter-nbextension", line 5, in <module>
    from notebook.nbextensions import main
ModuleNotFoundError: No module named 'notebook.nbextensions'


In [106]:
l.select()

ConceptSelectWidget(data='{"c8a0d6af-7908-48a9-b8d3-2f063884ba35": {"id": "c8a0d6af-7908-48a9-b8d3-2f063884ba3…

In [72]:
# You can also double-check on your selected concepts with this command
l.show_selected()



Active concepts (n=19):
- Safety and Health: Does the text involve safety measures, health studies, or emergency repairs?
- Environmental Management: Does the text discuss environmental restoration, waste management, or geotechnical studies?
- Specific Location: Does the text specify a particular location or address?
- Landscaping and Urbanization: Does the text involve landscaping or urban development?
- Carpentry and Installations: Does the text mention carpentry or installation of fixtures?
- Maintenance and Cleaning: Is the text about maintenance or cleaning of a facility?
- Flooring Work: Is the text about repairing or replacing flooring?
- Wood-Related Work: Does the text involve working with wood, either repairing or installing?
- Isolation Improvements: Does the text discuss improvements related to sound or climate isolation?
- Water Management: Does the example involve management or repair of water systems?
- Demolition Work: Is the example about demolition of any part of a 

### Score concepts
Then, apply these concepts to the full dataset with `score()`. This function will score all documents with respect to each concept to indicate the extent to which the document matches the concept inclusion criteria.

In [74]:
# Run concept scoring
score_df = await l.score()



Scoring 19 concepts for 100 documents
Estimated cost: $0.3
**Please note that this is only an approximate cost estimate**


Action required


Proceed with scoring? (y/n):  y


100%|██████████| 19/19 [03:09<00:00,  9.95s/it]
✅ Done with concept scoring!


In [75]:
# View cost/time summary
l.summary()

Total time: 222.41 sec (3.71 min)
	('Distill-summarize', '2024-09-11-17-14-54'): 3.69 sec
	('Cluster', '2024-09-11-17-15-05'): 11.63 sec
	('Synthesize', '2024-09-11-17-15-14'): 8.52 sec
	('Review-remove', '2024-09-11-17-15-15'): 0.80 sec
	('Review-merge', '2024-09-11-17-15-23'): 8.74 sec
	('Score', '2024-09-11-17-26-12'): 189.04 sec


Total cost: $0.74
	('Distill-summarize', '2024-09-11-17-14-54'): $0.010
	('Synthesize', '2024-09-11-17-15-14'): $0.064
	('Review-remove', '2024-09-11-17-15-15'): $0.007
	('Review-merge', '2024-09-11-17-15-23'): $0.016
	('Score-helper', '2024-09-11-17-23-14'): $0.034
	('Score-helper', '2024-09-11-17-23-23'): $0.035
	('Score-helper', '2024-09-11-17-23-34'): $0.034
	('Score-helper', '2024-09-11-17-23-43'): $0.034
	('Score-helper', '2024-09-11-17-23-54'): $0.034
	('Score-helper', '2024-09-11-17-24-00'): $0.034
	('Score-helper', '2024-09-11-17-24-15'): $0.034
	('Score-helper', '2024-09-11-17-24-23'): $0.034
	('Score-helper', '2024-09-11-17-24-31'): $0.034
	('S

### Visualize results
Now, you can visualize the results in the main **LLooM Workbench** view. An interactive widget will appear when you run the `vis` function:
![LLooM Workbench UI](https://github.com/michelle123lam/lloom/blob/main/docs/public/media/lloom_workbench_ui.png?raw=1)

The **Concept Overview (A)** provides a high-level summary. Click on a concept row in the **Concept Matrix (B)** to see its **Detail View (C)**, or click on a slice column to see its corresponding Detail View.

In [ ]:
# Visualize concept results
# Group data by the number of likes (automatically binned) with slice_col
l.vis(slice_col="sub_labels")
# l.vis()

In [ ]:
# Visualize concept results
# Group data by page category with slice_col
l.vis(slice_col="Page Category")

### (Optional) Try normalizing by slice or by concept


In [ ]:
l.vis()

In [ ]:
l.vis(norm_by="concept")

### (Optional) Add manual concept
You may also manually add your own custom concepts by providing a name and prompt. This will automatically score the data by that concept. Re-run the `vis()` function to see the new concept results.

In [ ]:
# Add a custom concept with the given name and prompt
await l.add(
    name="Your new concept name",
    prompt="Your new concept criteria prompt",  # Ex: "Does the text include [...]?"
)

In [ ]:
# Visualize concept results
l.vis(slice_col="Likes")

### (Optional) Submit your results
**🖼️ ✨ Submit your work for a chance to be featured on our site!**

If you'd like to share what you've done with LLooM or would like your work featured in a gallery of results, please submit your LLooM instance with the `submit()` function! If your submission is selected, we'll reach out to you to follow up and hear more about your work with LLooM.

In [ ]:
l.submit()  # You will be prompted to provide a few details about your analysis

### (Optional) Export and/or save results

In [77]:
l

In [ ]:
# Export the results to a dataframe
export_df = l.export_df()

In [ ]:
export_df.head()

In [ ]:
# Save the lloom to a pickle file
l.save(folder="your/path/here", file_name="your_file_name")

## v2: Auto mode

LLooM also provides a one-function **auto** mode that grants less control, but simplifies the generation and scoring process into a single function. You can try out this version with the functions below.

### Create a LLooM instance
Then, after loading your data as a Pandas DataFrame, create a new LLooM instance. You will need to specify the name of the column that contains your input text documents (`text_col`). The ID column (`id_col`) is optional.

In [101]:
# Set up the LLooM instance with the specified dataset
l = wb.lloom(
    df=df,
    text_col="text",
    id_col="doc_id",  # Optional
)

### Run concept generation
Next, you can go ahead and start the concept induction process by generating concepts. You can omit the `seed` parameter if you do not want to use a seed.

In [93]:
cur_seed = None  # Optionally replace with string
score_df = await l.gen_auto(seed=cur_seed, max_concepts=5)

N sentences: Median=1, Std=1.08
Auto-suggested parameters: {'filter_n_quotes': 1, 'summ_n_bullets': 1, 'synth_n_concepts': 6}


Estimated cost: $10.32
**Please note that this is only an approximate cost estimate**


Action required


Proceed with generation? (y/n):  n


Cancelled generation


ValueError: Sample larger than population or is negative

In [80]:
# View cost/time summary
l.summary()

Total time: 85.50 sec (1.42 min)
	('Distill-summarize', '2024-09-11-17-27-01'): 3.27 sec
	('Cluster', '2024-09-11-17-27-08'): 7.33 sec
	('Synthesize', '2024-09-11-17-27-19'): 10.72 sec
	('Review-remove', '2024-09-11-17-27-20'): 0.87 sec
	('Review-merge', '2024-09-11-17-27-32'): 12.41 sec
	('Score', '2024-09-11-17-32-14'): 50.89 sec


Total cost: $0.26
	('Distill-summarize', '2024-09-11-17-27-01'): $0.010
	('Synthesize', '2024-09-11-17-27-19'): $0.054
	('Review-remove', '2024-09-11-17-27-20'): $0.005
	('Review-merge', '2024-09-11-17-27-32'): $0.015
	('Score-helper', '2024-09-11-17-31-30'): $0.034
	('Score-helper', '2024-09-11-17-31-40'): $0.034
	('Score-helper', '2024-09-11-17-31-52'): $0.034
	('Score-helper', '2024-09-11-17-32-00'): $0.034
	('Score-helper', '2024-09-11-17-32-14'): $0.035


Tokens: total=243025, in=179885, out=63140


### Visualize results
Now, you can visualize the results in the main **LLooM Workbench** view. An interactive widget will appear when you run the `vis` function:
![LLooM Workbench UI](https://github.com/michelle123lam/lloom/blob/main/docs/public/media/lloom_workbench_ui.png?raw=1)

The **Concept Overview (A)** provides a high-level summary. Click on a concept row in the **Concept Matrix (B)** to see its **Detail View (C)**, or click on a slice column to see its corresponding Detail View.

In [ ]:
# Visualize concept results
# Group data by the number of likes (automatically binned) with slice_col
l.vis(slice_col="Likes")

In [ ]:
# Visualize concept results
# Group data by page category with slice_col
l.vis(slice_col="Page Category")

### (Optional) Try normalizing by slice or by concept


In [ ]:
l.vis(slice_col="Likes", norm_by="slice")

In [ ]:
l.vis(norm_by="concept")

### (Optional) Add manual concept
You may also manually add your own custom concepts by providing a name and prompt. This will automatically score the data by that concept. Re-run the `vis()` function to see the new concept results.

In [ ]:

# Add a custom concept with the given name and prompt
await l.add(
    name="Your new concept name",
    prompt="Your new concept criteria prompt",  # Ex: "Does the text include [...]?"
)

In [ ]:
# Visualize concept results
l.vis(slice_col="Likes")

### (Optional) Submit your results
**🖼️ ✨ Submit your work for a chance to be featured on our site!**

If you'd like to share what you've done with LLooM or would like your work featured in a gallery of results, please submit your LLooM instance with the `submit()` function! If your submission is selected, we'll reach out to you to follow up and hear more about your work with LLooM.

In [ ]:
l.submit()  # You will be prompted to provide a few details about your analysis

### (Optional) Export and/or save results

In [ ]:
# Export the results to a dataframe
export_df = l.export_df()

In [ ]:
export_df.head()

In [ ]:
# Save the lloom to a pickle file
l.save(folder="your/path/here", file_name="your_file_name")